<a href="https://colab.research.google.com/github/SXV357/Inspirit-AI-Deep-Dive-Designing-DL-Systems-FinalProject-RL-for-Autonomous-Vehicles/blob/main/DQN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!echo Downloading stuff...
!wget 'https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/Deep%20Dives/Advanced%20Topics%20in%20AI/Sessions%206%20-%2010%20(Projects)/Project%20-%20Self%20Driving%20Cars/rl.zip' -O temp > /dev/null 2>&1
!unzip temp -d rl > /dev/null 2>&1

!wget 'https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/Deep%20Dives/Advanced%20Topics%20in%20AI/Sessions%206%20-%2010%20(Projects)/Project%20-%20Self%20Driving%20Cars/training_results.zip' -O training_results.zip > /dev/null 2>&1
!unzip training_results.zip -d training_results > /dev/null 2>&1

!wget 'https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/Deep%20Dives/Advanced%20Topics%20in%20AI/Sessions%206%20-%2010%20(Projects)/Project%20-%20Self%20Driving%20Cars/videos.zip' -O videos.zip > /dev/null 2>&1
!unzip videos.zip -d videos > /dev/null 2>&1

!wget 'https://storage.googleapis.com/inspirit-ai-data-bucket-1/Data/Deep%20Dives/Advanced%20Topics%20in%20AI/Sessions%206%20-%2010%20(Projects)/Project%20-%20Self%20Driving%20Cars/checkpoints.zip' -O checkpoints.zip > /dev/null 2>&1
!unzip checkpoints.zip -d checkpoints > /dev/null 2>&1


!echo Installing packages... 

!pip install Box2D > /dev/null 2>&1
!pip install gym[box2d] pyvirtualdisplay > /dev/null 2>&1
!apt-get update > /dev/null 2>&1
!apt-get install -y xvfb python-opengl ffmpeg > /dev/null 2>&1
!pip install plotly --upgrade > /dev/null 2>&1

!echo Done!
!ls

Installing packages...
Done!
checkpoints	 sample_data	   training_results.zip
checkpoints.zip  temp		   videos
rl		 training_results  videos.zip


In [2]:
INDEX2STRING = [
    "stay",
    "accelerate",
    "right",
    "left",
]

import gym 
import plotly.express as px
import numpy as np
import warnings
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from collections import Counter, defaultdict
import pandas as pd
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.optimizers import Adam
import datetime
from sklearn.metrics import confusion_matrix
import plotly.figure_factory as ff
from tqdm import tqdm

import os
import pickle
import random
import sys

import gym
import numpy as np
import plotly.express as px
from gym.wrappers import Monitor
from tensorflow.keras.layers import (
    Activation,
    BatchNormalization,
    Conv2D,
    Dense,
    Dropout,
    Flatten,
    Lambda,
    MaxPool2D,
    Permute,
    Reshape,
)
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
import json 
from rl.agents.dqn import DQNAgent
from rl.callbacks import Callback, FileLogger, ModelIntervalCheckpoint
from rl.memory import SequentialMemory
from rl.policy import BoltzmannQPolicy, EpsGreedyQPolicy, LinearAnnealedPolicy, Policy
from rl.processors import Processor

import glob
from IPython import display as ipythondisplay
from tqdm.notebook import tqdm
from gym.wrappers import Monitor
from IPython.display import HTML
import base64
import io
import pickle
warnings.filterwarnings("ignore")
from pyvirtualdisplay import Display

display = Display(visible=0, size=(1400, 900))
display.start()


INDEX2STRING = [
    "stay",
    "accelerate",
    "right",
    "left",
]
INDEX2ACTIONS = [
    (0, 0, 0),
    (0, 1, 0),
    (1, 0, 0),
    (-1, 0, 0),
]

def run_blackjack(policy, show=False):
    env = gym.make("Blackjack-v0")
    obs = env.reset()
    history = []
    while True:
        move = policy(obs)
        new_obs, reward, done, info = env.step(move)
        history.append((obs, move, new_obs, done, reward))
        obs = new_obs
        if done:
            break
    if show:
        result = history[-1][-1]
        if result > 0:
            print("Congrats! You win")
        if result == 0:
            print("Tie!")
        if result < 0:
            print("You lose!")
        print("Your cards: ", env.player)
        print("Dealers cards", env.dealer)

    env.close()
    return history

def human_blackjack_player(obs):
    print(f"Your total: {obs[0]}")
    print(f"Dealer card: {obs[1]}")
    print(f"Usable ace?: {obs[2]}")
    return int(input("0 for stay 1 for hit: "))


def load_pkl(fname):
    with open(fname, "rb") as f:
        return pickle.load(f)
"""
Utility functions to enable video recording of gym environment and displaying it
To enable video, just do "env = wrap_env(env)""
"""

def show_video():
  mp4list = glob.glob('video/*.mp4')
  if len(mp4list) > 0:
    mp4 = mp4list[0]
    video = io.open(mp4, 'r+b').read()
    encoded = base64.b64encode(video)
    ipythondisplay.display(HTML(data='''<video alt="test" autoplay 
                loop controls style="height: 400px;">
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii'))))
  else: 
    print("Could not find video")

def play_mp4(mp4):
  video = io.open(mp4, 'r+b').read()
  encoded = base64.b64encode(video)
  ipythondisplay.display(HTML(data='''<video alt="test" autoplay 
                loop controls style="height: 400px;">
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii'))))

def wrap_env(env):
  env = Monitor(env, './video', force=True)
  return env


def run_racing(policy, max_steps=1000):
    env = gym.make("CarRacing-v0")
    env = wrap_env(env)
    obs = env.reset() # Intialize the observation
    for step in tqdm(range(min(max_steps, 1000))):
        env.render()

        move = policy(obs, env, step)
        obs, reward, done, info = env.step(move)
        if done:
            break

    env.close()
    show_video()

def load_json(fname):
    with open(fname, "r") as f:
        return json.load(f)


In [3]:
#@title Double click here for idea

''' 
If I'm at state $s$, I can use $Q$ to check which action $a$ has the highest quality, and then choose that action to perform!
Mathematically, I want to pick the action $a$ that maximizes $Q(s, a)$.
'''


" \nIf I'm at state $s$, I can use $Q$ to check which action $a$ has the highest quality, and then choose that action to perform!\nMathematically, I want to pick the action $a$ that maximizes $Q(s, a)$.\n"

In [4]:
def q_policy(s, q):
    ## BEGIN CODE HERE
    return q[(s, 0)] >= q[(s, 1)]
    ## END CODE HERE

    # return 0 if q[(obs, 0)] >= q[(obs, 1)] else 1(o returns higher q score than 1)
    #quality of taking action 0 > action 1(policy towards returning 0)
    # possible actions --> -1,0,1



In [5]:
history = run_blackjack(human_blackjack_player, show=True)

Your total: 17
Dealer card: 1
Usable ace?: False
0 for stay 1 for hit: 0
Tie!
Your cards:  [7, 10]
Dealers cards [1, 4, 10, 2]


In [6]:
print(history[0])

((17, 1, False), 0, (17, 1, False), True, 0.0)


In [7]:
def print_hist(h):
  print(f"The state was: {h[0]}")
  print(f"The action was: {h[1]}")
  print(f"The state is now: {h[2]}")
  print(f"The episode is over: : {h[3]}")
  print(f"Reward for this action: {h[4]}")

print_hist(history[0])

The state was: (17, 1, False)
The action was: 0
The state is now: (17, 1, False)
The episode is over: : True
Reward for this action: 0.0


In [8]:
def eps_policy(s, q, eps):
    if random.random() < eps: # pick on interval between 0 and 1(if beta within sub interval, take random action and its probability is epsilon)
       return random.choice([0, 1])
    else:
      return q_policy(s, q) # use best estimate of q


In [9]:
def q_learn_blackjack(eps, gamma, alpha, epochs):
    q_table = defaultdict(int)
    training_results = []
    for _ in tqdm(range(epochs)):
        # history contains the (s, a, s_next, done, r) tuples that we saw ealier for a particular run of the game
        history = run_blackjack(lambda obs: eps_policy(obs, q_table, eps))
        for s, a, s_next, done, r in reversed(history):
            old = q_table[(s, a)]
            if done:  # Don't care about the best next b/c we're done!
                q_table[(s, a)] = (1 - alpha) * old + alpha * (r)
            else:
                best_next = max([q_table[(s_next, 0)], q_table[(s_next, 1)]])
                q_table[(s, a)] = (1 - alpha) * old + alpha * (r + gamma * best_next)
        training_results.append(history[-1][-1])
    return q_table, training_results

In [10]:
EPS = 0.7
GAMMA = 1
ALPHA = 0.2
EPOCHS = 50000
q_table, results = q_learn_blackjack(EPS, GAMMA, ALPHA, EPOCHS)

  0%|          | 0/50000 [00:00<?, ?it/s]

In [11]:
q_table

defaultdict(int,
            {((4, 1, False), 0): -0.67232,
             ((4, 1, False), 1): -0.30007086128474497,
             ((4, 2, False), 0): -0.3519898624,
             ((4, 2, False), 1): 0.11883696445873279,
             ((4, 3, False), 0): -0.6560601819436706,
             ((4, 3, False), 1): -0.03865431159004526,
             ((4, 4, False), 0): -0.7685975639654401,
             ((4, 4, False), 1): -0.04815421951585939,
             ((4, 5, False), 0): -0.6776677376,
             ((4, 5, False), 1): 0.03196733112741034,
             ((4, 6, False), 0): -0.11765276396093455,
             ((4, 6, False), 1): 0.20272569587378925,
             ((4, 7, False), 0): -0.7287858176000002,
             ((4, 7, False), 1): 0.0034741270742571183,
             ((4, 8, False), 0): -0.742536843264,
             ((4, 8, False), 1): 0.000668706904479538,
             ((4, 9, False), 0): -0.9181654111289346,
             ((4, 9, False), 1): -0.14914636110301616,
             ((4, 10, False), 

In [12]:
run_blackjack(lambda s : q_policy(s, q_table), show=1)

You lose!
Your cards:  [2, 7]
Dealers cards [5, 2, 2, 3, 7]


[((9, 5, False), False, (9, 5, False), True, -1.0)]

# Deep Q-Learning

In [13]:
ENV_NAME = "CarRacing-v0"
INPUT_SHAPE = (96, 96, 3)
WINDOW_LENGTH = 3
VIDEO_INTERVAL = 25 # in episodes
TRAIN_STEPS = 175000
ANNEAL_STEPS = 100000
NB_ACTIONS = 4


class RacingProcessor(Processor):
    def __init__(self, env):
        self.env = env
        self.count = 0

    def process_action(self, action):
        return INDEX2ACTIONS[action]


def start_policy(state):
    return 1

def get_driving_env_dqn(name, grass_penalty, still_penalty):
    env = Monitor(RewardWrapper(gym.make(ENV_NAME), grass_penalty, still_penalty), f"/home/harry/Documents/videos/{name}", lambda x: x % VIDEO_INTERVAL==0, force=True)
    return env

NB_ACTIONS = 4

# Next, we build a very simple model.
# model = Sequential(
#     [
#         Permute((2, 3, 1, 4), input_shape=(WINDOW_LENGTH, 96, 96, 3)),
#         Reshape((96, 96, -1)),
#         Lambda(lambda x: x / 255.0),
#         MaxPool2D(2),
#         Conv2D(32, 3, activation="relu"),
#         MaxPool2D(2),
#         # Dropout(0.2),
#         Conv2D(64, 3, activation="relu"),
#         MaxPool2D(2),
#         # Dropout(0.2),
#         Conv2D(64, 3, activation="relu"),
#         Flatten(),
#         Dense(32, activation="relu"),
#         Dense(NB_ACTIONS),
#     ]
# )
# print(model.summary())

memory = SequentialMemory(limit=50000, window_length=WINDOW_LENGTH)
# policy = BoltzmannQPolicy()
annealed_policy = LinearAnnealedPolicy(
    EpsGreedyQPolicy(),
    attr="eps",
    value_max=1,
    value_min=0.1,
    value_test=0.05,
    nb_steps=ANNEAL_STEPS,
)
eps_greedy_policy = EpsGreedyQPolicy(0.1)

small_eps = EpsGreedyQPolicy(0)


def get_dqn(env, policy, model, test_policy='regular'):
    if test_policy == 'regular':
      tp = small_eps
    else:
      tp = SpeedLimitPolicy(env, 3000)
    dqn = DQNAgent(
        model=model,
        nb_actions=NB_ACTIONS,
        policy=policy,
        memory=memory,
        processor=RacingProcessor(env),
        nb_steps_warmup=100,
        gamma=0.95,
        target_model_update=10000,
        train_interval=4,
        # delta_clip=1.0,
        test_policy=tp,
        enable_dueling_network=True
    )

    dqn.compile(Adam(learning_rate=1e-4), metrics=["mae"])
    return dqn


def load(dqn, fname):
    dqn.load_weights(fname)
    return dqn


def train(env, dqn, name, action_rep):
    # log_path = f"driving_models/{name}.log"
    # checkpoint_path= f"/home/harry/Documents/driving_models/{name}.cpt"
    callbacks = [
        # ModelIntervalCheckpoint(checkpoint_path, interval=10000),
        # FileLogger(log_path, interval=1000),
    ]
    history = dqn.fit(
        env,
        nb_steps=TRAIN_STEPS,
        visualize=True,
        verbose=2,
        action_repetition=action_rep,
        nb_max_episode_steps=None,
        callbacks=callbacks,
    )
    # dqn.save_weights(checkpoint_path, overwrite=True)

class SpeedLimitPolicy(Policy):
    """Implement the greedy policy

    Greedy policy returns the current best action according to q_values
    """

    def __init__(self, env, max_speed, eps=0):
        self.max_speed = max_speed
        self.env = env
        self.eps = eps

    def select_action(self, q_values):
        """Return the selected action

        # Arguments
            q_values (np.ndarray): List of the estimations of Q for each action

        # Returns
            Selection action
        """
        if np.random.uniform() < self.eps:
            return np.random.randint(0, NB_ACTIONS)
        else:
            speed = get_features_from_env(env)[0]
            order = np.argsort(q_values)
            best = order[-1]
            if speed > self.max_speed and best == 1:
                return order[-2]
            else:
                return best

def get_videos(name):
  videos = sorted([f'videos/{name}/{x}' for x in os.listdir(f"videos/{name}") if 'mp4' in x])
  print(f"There are {len(videos)} recorded video episodes")
  return(videos)

# Finally, evaluate our algorithm for 5 episodes.
def test(env, dqn, name):
    checkpoint_path= f"checkpoints/{name}.cpt"
    dqn = load(dqn, checkpoint_path)
    dqn.test(
        env,
        nb_episodes=1,
        visualize=False,
        action_repetition=4,
        # nb_max_start_steps=40,
        # start_step_policy=start_policy,
        nb_max_episode_steps=None,
    )

def get_features_from_env(env):
    wheel = env.car.wheels[0]
    speed = sum(map(lambda x: x ** 2, list(wheel.linearVelocity)))
    return [speed, wheel.angularVelocity] + list(wheel.linearVelocity)

In [14]:
ENV_NAME = "CarRacing-v0"
INPUT_SHAPE = (96, 96, 3)
WINDOW_LENGTH = 3
VIDEO_INTERVAL = 25  # in episodes
TRAIN_STEPS = 175000
ANNEAL_STEPS = 100000
env = gym.make('CarRacing-v0')
env = wrap_env(env)

annealed_policy = LinearAnnealedPolicy(
    EpsGreedyQPolicy(),
    attr="eps",
    value_max=1,
    value_min=0.1,
    value_test=0.05,
    nb_steps=ANNEAL_STEPS,
)

model = Sequential(
    [
        Permute((2, 3, 1, 4), input_shape=(WINDOW_LENGTH, 96, 96, 3)), #(h, w, window, rgb)
        Reshape((96, 96, -1)), # Flatten the window dimension
        Lambda(lambda x: x / 255.0), # Normalize
        MaxPool2D(2), # Compress image
        Conv2D(32, 3, activation="relu"),
        MaxPool2D(2),
        # Dropout(0.2),
        Conv2D(64, 3, activation="relu"),
        MaxPool2D(2),
        # Dropout(0.2),
        Conv2D(64, 3, activation="relu"),
        Flatten(),
        Dense(32, activation="relu"),
        Dense(NB_ACTIONS),
    ]
)
model.summary()


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 permute (Permute)           (None, 96, 96, 3, 3)      0         
                                                                 
 reshape (Reshape)           (None, 96, 96, 9)         0         
                                                                 
 lambda (Lambda)             (None, 96, 96, 9)         0         
                                                                 
 max_pooling2d (MaxPooling2D  (None, 48, 48, 9)        0         
 )                                                               
                                                                 
 conv2d (Conv2D)             (None, 46, 46, 32)        2624      
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 23, 23, 32)       0         
 2D)                                                    

In [15]:
dqn = get_dqn(env, annealed_policy, model)

In [16]:
baseline_videos = get_videos("baseline_repeat")

There are 12 recorded video episodes


In [17]:
play_mp4(baseline_videos[11])

In [18]:
test(env, dqn, 'baseline_repeat')
env.close()
show_video()

Testing for 1 episodes ...
Track generation: 937..1183 -> 246-tiles track
Episode 1: reward: -95.120, steps: 111


In [19]:
x  = load_json('training_results/baseline_repeat.log')
px.line(pd.DataFrame(x))

In [20]:
ROAD_COLORS = [(102 + i, 102 + i, 102 + i) for i in range(6)]

class PenalizeLeavingRoad(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)


    def reward(self, rew):
        left_col = tuple(self.env.state[65, 50, :])
        right_col = tuple(self.env.state[65, 45, :])
        if left_col not in ROAD_COLORS or right_col not in ROAD_COLORS:
          return -1000
        else:
          return rew


In [21]:
safe_videos = get_videos("safe2")

There are 33 recorded video episodes


In [22]:
play_mp4(safe_videos[32])

In [23]:
x  = load_json('training_results/safe2.log')
px.line(pd.DataFrame(x))

In [24]:
env = wrap_env(gym.make("CarRacing-v0"))
dqn = get_dqn(env, annealed_policy, model) # anneal policy makes it smoother
test(env, dqn, 'safe2')
env.close()
show_video()

Testing for 1 episodes ...
Track generation: 1244..1559 -> 315-tiles track
Episode 1: reward: 699.363, steps: 250


In [25]:
class PenalizeNotMoving(gym.RewardWrapper):
    def __init__(self, env, grass_penalty, still_penalty):
        super().__init__(env)

    def reward(self, rew):
        left_col = tuple(self.env.state[65, 50, :])
        right_col = tuple(self.env.state[65, 45, :])
        if left_col not in ROAD_COLORS or right_col not in ROAD_COLORS:
            return -1000
        if is_still(rew):
            return -0.1
        return rew

In [26]:
mix_videos = get_videos("mix")

There are 35 recorded video episodes


In [27]:
play_mp4(mix_videos[25])

In [28]:
x  = load_json('training_results/mix.log')
px.line(pd.DataFrame(x))

In [29]:
env = wrap_env(gym.make("CarRacing-v0"))
dqn = get_dqn(env, annealed_policy, model)
test(env, dqn, 'mix')
env.close()
show_video()

Testing for 1 episodes ...
Track generation: 1159..1452 -> 293-tiles track
Episode 1: reward: 865.753, steps: 250
